In [ ]:
!git clone https://github.com/Aniruddha-Ponnuri/Amazon--ML--challenge.git

Cloning into 'Amazon--ML--challenge'...
remote: Enumerating objects: 949, done.
remote: Total 949 (delta 0), reused 0 (delta 0), pack-reused 949 (from 1)
Receiving objects: 100% (949/949), 245.09 MiB | 51.01 MiB/s, done.
Resolving deltas: 100% (2/2), done.
Updating files: 100% (943/943), done.


In [ ]:
import pandas as pd
import numpy as np
import requests
from io import BytesIO
from PIL import Image
import re
import tensorflow as tf
from tensorflow.keras.applications.resnet50 import ResNet50, preprocess_input
from tensorflow.keras.layers import Dense, GlobalAveragePooling2D, Dropout, Input
from tensorflow.keras.models import Model
from tensorflow.keras.optimizers import Adam
from sklearn.preprocessing import LabelEncoder
from sklearn.model_selection import train_test_split
from tqdm import tqdm
import os
import sys
sys.path.append('/content/Amazon--ML--challenge/')
from src.utils import parse_string
from src.constants import entity_unit_map
from src.sanity import sanity_check
import warnings
warnings.filterwarnings('ignore')

In [ ]:
# 1. Load Data
train_df = pd.read_csv('/content/Amazon--ML--challenge/dataset/train.csv')
test_df = pd.read_csv('/content/Amazon--ML--challenge/dataset/test.csv')
image_dir = '/content/Amazon--ML--challenge/images'

In [ ]:
# 2. Process Images Directly from URLs
def load_and_preprocess_image_from_url(url):
    try:
        response = requests.get(url, timeout=10)
        img = Image.open(BytesIO(response.content)).convert('RGB')
        img = img.resize((224, 224))
        img_array = np.array(img)
        img_array = np.expand_dims(img_array, axis=0)
        img_array = preprocess_input(img_array)
        return img_array
    except Exception as e:
        print(f"Error loading image from {url}: {e}")
        # Create a black placeholder image
        img = Image.new('RGB', (224, 224), color='black')
        img_array = np.array(img)
        img_array = np.expand_dims(img_array, axis=0)
        img_array = preprocess_input(img_array)
        return img_array

In [ ]:
# Map image filenames (group_id) to image paths
train_df['image_path'] = train_df['group_id'].apply(lambda x: os.path.join(image_dir, f'{x}.jpg'))

In [ ]:
# 2. Preprocess Images from Local Files
def load_and_preprocess_local_image(image_path):
    try:
        img = Image.open(image_path).convert('RGB')
        img = img.resize((224, 224))  # ResNet input size
        img_array = np.array(img)
        img_array = np.expand_dims(img_array, axis=0)  # Add batch dimension
        img_array = preprocess_input(img_array)
        return img_array
    except Exception as e:
        print(f"Error loading image from {image_path}: {e}")
        # Create a black placeholder image
        img = Image.new('RGB', (224, 224), color='black')
        img_array = np.array(img)
        img_array = np.expand_dims(img_array, axis=0)
        img_array = preprocess_input(img_array)
        return img_array

In [ ]:
# 3. Extract Features Using ResNet50
base_model = ResNet50(weights='imagenet', include_top=False, input_shape=(224, 224, 3))


94765736/94765736 [==============================] - 0s 0us/step


In [ ]:
# 4. Prepare Labels for Training
def extract_value_and_unit(entity_value):
    pattern = r'^(\d+\.?\d*)\s+([a-zA-Z\s]+)$'
    match = re.match(pattern, str(entity_value).strip())
    if match:
        value = float(match.group(1))
        unit = match.group(2).strip().lower()
        return value, unit
    else:
        return None, None

In [ ]:
train_df['value_unit'] = train_df['entity_value'].apply(extract_value_and_unit)
train_df = train_df.dropna(subset=['value_unit'])
train_df['value'] = train_df['value_unit'].apply(lambda x: x[0])
train_df['unit'] = train_df['value_unit'].apply(lambda x: x[1])
train_df = train_df.drop(columns=['value_unit'])

In [ ]:
train_df.head()

image_link  group_id  entity_name  \
0  https://m.media-amazon.com/images/I/61I9XdN6OF...    748919  item_weight   
1  https://m.media-amazon.com/images/I/71gSRbyXmo...    916768  item_volume   
2  https://m.media-amazon.com/images/I/61BZ4zrjZX...    459516  item_weight   
3  https://m.media-amazon.com/images/I/612mrlqiI4...    459516  item_weight   
4  https://m.media-amazon.com/images/I/617Tl40LOX...    731432  item_weight   

     entity_value                                        image_path     value  \
0      500.0 gram  /content/Amazon--ML--challenge/images/748919.jpg   500.000   
1         1.0 cup  /content/Amazon--ML--challenge/images/916768.jpg     1.000   
2      0.709 gram  /content/Amazon--ML--challenge/images/459516.jpg     0.709   
3      0.709 gram  /content/Amazon--ML--challenge/images/459516.jpg     0.709   
4  1400 milligram  /content/Amazon--ML--challenge/images/731432.jpg  1400.000   

        unit  
0       gram  
1        cup  
2       gram  
3       gram  
4  milligram

In [ ]:
# Encode units per entity_name
from collections import defaultdict

unit_encoders = defaultdict(LabelEncoder)

def encode_unit(row):
    entity = row['entity_name']
    unit = row['unit']
    le = unit_encoders[entity]
    # Check if the LabelEncoder has been fitted
    if not hasattr(le, 'classes_') or len(le.classes_) == 0:
        le.fit(train_df[train_df['entity_name'] == entity]['unit'].unique())
    return le.transform([unit])[0]


train_df['unit_encoded'] = train_df.apply(encode_unit, axis=1)

In [ ]:
train_df.head()

image_link  group_id  entity_name  \
0  https://m.media-amazon.com/images/I/61I9XdN6OF...    748919  item_weight   
1  https://m.media-amazon.com/images/I/71gSRbyXmo...    916768  item_volume   
2  https://m.media-amazon.com/images/I/61BZ4zrjZX...    459516  item_weight   
3  https://m.media-amazon.com/images/I/612mrlqiI4...    459516  item_weight   
4  https://m.media-amazon.com/images/I/617Tl40LOX...    731432  item_weight   

     entity_value                                        image_path     value  \
0      500.0 gram  /content/Amazon--ML--challenge/images/748919.jpg   500.000   
1         1.0 cup  /content/Amazon--ML--challenge/images/916768.jpg     1.000   
2      0.709 gram  /content/Amazon--ML--challenge/images/459516.jpg     0.709   
3      0.709 gram  /content/Amazon--ML--challenge/images/459516.jpg     0.709   
4  1400 milligram  /content/Amazon--ML--challenge/images/731432.jpg  1400.000   

        unit  unit_encoded  
0       gram             7  
1        cup             3  
2       gram             7  
3       gram             7  
4  milligram            12

In [ ]:
# 6. Extract Features for Training Images
print("Extracting features from training images...")
train_features = []
train_values = []
train_units = []
for idx, row in tqdm(train_df.iterrows(), total=train_df.shape[0]):
    image_path = row['image_path']
    img_array = load_and_preprocess_local_image(image_path)
    features = base_model.predict(img_array)
    features = features.reshape(-1)
    train_features.append(features)
    train_values.append(row['value'])
    train_units.append(row['unit_encoded'])

X_train = np.array(train_features)
y_value = np.array(train_values).astype('float32')
y_unit = np.array(train_units).astype('int32')

Extracting features from training images...


  0%|          | 0/263859 [00:00<?, ?it/s]

1/1 [==============================] - 1s 1s/step


  0%|          | 1/263859 [00:01<117:22:52,  1.60s/it]

1/1 [==============================] - 0s 90ms/step


...

1/1 [==============================] - 0s 86ms/step


  5%|▍         | 12795/263859 [45:27<16:09:16,  4.32it/s]

1/1 [==============================] - 0s 107ms/step


  5%|▍         | 12796/263859 [45:28<18:07:11,  3.85it/s]

1/1 [==============================] - ETA: 0s

In [ ]:
# 7. Build and Train the Model
input_shape = X_train.shape[1]
inputs = Input(shape=(input_shape,))

x = Dense(1024, activation='relu')(inputs)
x = Dropout(0.5)(x)

value_output = Dense(1, name='value_output')(x)

max_unit_classes = max([len(le.classes_) for le in unit_encoders.values()])
unit_output = Dense(max_unit_classes, activation='softmax', name='unit_output')(x)

model = Model(inputs=inputs, outputs=[value_output, unit_output])

model.compile(optimizer=Adam(learning_rate=1e-4),
              loss={'value_output': 'mean_squared_error', 'unit_output': 'sparse_categorical_crossentropy'},
              loss_weights={'value_output': 1.0, 'unit_output': 1.0})

# Split data
X_train_split, X_val_split, y_value_train, y_value_val, y_unit_train, y_unit_val = train_test_split(
    X_train, y_value, y_unit, test_size=0.2, random_state=42)

# Train the model
epochs = 25
batch_size = 32

print("Training the model...")
history = model.fit(X_train_split, {'value_output': y_value_train, 'unit_output': y_unit_train},
                    validation_data=(X_val_split, {'value_output': y_value_val, 'unit_output': y_unit_val}),
                    epochs=epochs, batch_size=batch_size)

In [ ]:
# 7. Predict Entity Values for test.csv
print("Extracting features from test images...")
test_features = []
entity_names = []
for idx, row in tqdm(test_df.iterrows(), total=test_df.shape[0]):
    image_link = row['image_link']
    entity_name = row['entity_name']
    entity_names.append(entity_name)
    img_array = load_and_preprocess_image_from_url(image_link)
    features = base_model.predict(img_array)
    features = features.reshape(-1)
    test_features.append(features)

X_test = np.array(test_features)

In [ ]:
# Make predictions
print("Making predictions on test data...")
pred_values, pred_units_probs = model.predict(X_test)

# 8. Format Predictions According to Challenge Rules
# Map predicted units back to actual unit labels
predicted_units = []
for i, entity_name in enumerate(entity_names):
    le = unit_encoders.get(entity_name)
    if le is not None:
        unit_probs = pred_units_probs[i]
        num_classes = len(le.classes_)
        unit_index = np.argmax(unit_probs[:num_classes])
        unit = le.inverse_transform([unit_index])[0]
    else:
        unit = ''
    predicted_units.append(unit)

In [ ]:
# Combine predicted values and units
pred_values_formatted = [str(round(val[0], 2)) for val in pred_values]

predictions = []
for value, unit, entity_name in zip(pred_values_formatted, predicted_units, entity_names):
    allowed_units = entity_unit_map[entity_name]
    if unit in allowed_units:
        prediction = f"{value} {unit}"
        try:
            parse_string(prediction)
            predictions.append(prediction)
        except ValueError:
            predictions.append('')
    else:
        predictions.append('')

In [ ]:
# 9. Save Predictions to CSV
output_df = pd.DataFrame({
    'index': test_df['index'],
    'prediction': predictions
})

assert len(output_df) == len(test_df), "Mismatch in number of predictions."

output_df.to_csv('test_out.csv', index=False)
print("Predictions saved to test_out.csv")


In [ ]:
# 10. Run Sanity Checker
print("Running sanity checker...")
try:
    sanity_check('dataset/test.csv', 'test_out.csv')
    print("Sanity check passed.")
except Exception as e:
    print(f"Sanity check failed: {e}")